In [7]:
import os
import logging

import psycopg2
import psycopg2.extensions
from pymongo import MongoClient
import pandas as pd
from sqlalchemy import create_engine
from sqlalchemy import Table, Column, Integer, Float, MetaData, String
from sqlalchemy.orm import sessionmaker
from sqlalchemy.ext.declarative import declarative_base


logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
logger = logging.getLogger(__name__)

In [12]:
# Задание по Psycopg2
# --------------------------------------------------------------

logger.info("Создаём подключёние к Postgres")
params = {
    "host": "localhost", #os.environ['APP_POSTGRES_HOST'],
    "port": "5433", #os.environ['APP_POSTGRES_PORT'],
    "user": 'postgres'
}
conn = psycopg2.connect(**params)

# дополнительные настройки
psycopg2.extensions.register_type(
    psycopg2.extensions.UNICODE,
    conn
)
conn.set_isolation_level(
    psycopg2.extensions.ISOLATION_LEVEL_AUTOCOMMIT
)
cursor = conn.cursor()

# ВАШ КОД ЗДЕСЬ
# -------------
# таблица movies_top
# movieId (id фильма), ratings_num(число рейтингов), ratings_avg (средний рейтинг фильма)

sql_str = "select * into movies_top from (select movieId, count(rating) ratings_num, avg(rating) ratings_avg from ratings group by movieId) t"

# -------------

cursor.execute(sql_str)
conn.commit()

# Проверка - выгружаем данные
cursor.execute("SELECT * FROM movies_top LIMIT 10")
logger.info(
    "Выгружаем данные из таблицы movies_top: (movieId, ratings_num, ratings_avg)\n{}".format(
        [i for i in cursor.fetchall()])
)



2018-12-25 23:57:17,792 : INFO : Создаём подключёние к Postgres
2018-12-25 23:57:18,864 : INFO : Выгружаем данные из таблицы movies_top: (movieId, ratings_num, ratings_avg)
[(790, 6, 3.16666666666667), (146688, 2, 3.25), (69906, 1, 5.0), (139056, 1, 3.0), (165533, 1, 3.0), (4790, 5, 2.7), (26745, 5, 3.3), (3936, 18, 3.44444444444444), (88837, 3, 3.16666666666667), (31297, 1, 4.5)]


In [16]:
os.environ['APP_POSTGRES_HOST'] = 'localhost'
os.environ['APP_POSTGRES_PORT'] = '5433'

In [20]:

# Задание по SQLAlchemy
# --------------------------------------------------------------
Base = declarative_base()


class MoviesTop(Base):
    __tablename__ = 'movies_top'

    movieid = Column(Integer, primary_key=True)
    ratings_num = Column(Float)
    ratings_avg = Column(Float)

    def __repr__(self):
        return "<User(movieid='%s', ratings_num='%s', ratings_avg='%s')>" % (self.movieid, self.ratings_num, self.ratings_avg)


# Создаём сессию

engine = create_engine('postgresql://postgres:@{}:{}'.format(os.environ['APP_POSTGRES_HOST'], os.environ['APP_POSTGRES_PORT']))
Session = sessionmaker(bind=engine)
session = Session()


# --------------------------------------------------------------
# Ваш код здесь
# выберите контент у которого больше 15 оценок (используйте filter)
# и средний рейтинг больше 3.5 (filter ещё раз)
# отсортированный по среднему рейтингу (используйте order_by())
# id такого контента нужно сохранить в массив top_rated_content_ids

# MoviesTop = "select movieId filter (where ratings_num > 15 and ratings_avg > ) from movies_top"

top_rated_query = session.query(MoviesTop).filter(MoviesTop.ratings_num > 15).filter(MoviesTop.ratings_avg > 3.5).order_by(MoviesTop.ratings_avg.desc())


logger.info("Выборка из top_rated_query\n{}".format([i for i in top_rated_query.limit(4)]))

top_rated_content_ids = [
    i[0] for i in top_rated_query.values(MoviesTop.movieid)
][:5]
# --------------------------------------------------------------



2018-12-27 22:41:52,564 : INFO : Выборка из top_rated_query
[<User(movieid='159817', ratings_num='23.0', ratings_avg='4.47826086956522')>, <User(movieid='2937', ratings_num='32.0', ratings_avg='4.46875')>, <User(movieid='38304', ratings_num='19.0', ratings_avg='4.44736842105263')>, <User(movieid='2330', ratings_num='31.0', ratings_avg='4.43548387096774')>]


In [39]:
os.environ['APP_MONGO_HOST'] = 'localhost'
os.environ['APP_MONGO_PORT'] = '27018'

In [48]:
# Задание по PyMongo
mongo = MongoClient(**{
    'host': os.environ['APP_MONGO_HOST'],
    'port': int(os.environ['APP_MONGO_PORT'])
})

# Получите доступ к коллекции tags
db = mongo.get_database(name="movie")

collection = db['tags']

agg_filename = 'keywords.csv'
tag_data = []
if db.tags.count() == 0:
    with open(agg_filename, 'r') as f:
        for line in f.readlines():
            try:
                movieId, tags = line.strip().split('\t')
                tags = eval(tags)
                for tag in tags:
                    print(tags)
                    tag.update({'movieId': movieId})
                    tag_data.append(
                        tag
                    )
            except:
                    print(line)
    collection.insert_many(tag_data)

# id контента используйте для фильтрации - передайте его в модификатор $in внутри find
# в выборку должны попать теги фильмов из массива top_rated_content_ids
mongo_query = tags_collection.count()#find(
        #{'id': {'$in': top_rated_content_ids}}
#)

# mongo_docs = [
  #  i for i in mongo_query
#]

#print("Достали документы из Mongo: {}".format(mongo_docs[:5]))
print(mongo_query)
#id_tags = [(i['id'], i['name']) for i in mongo_docs]



/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:14: DeprecationWarning: count is deprecated. Use estimated_document_count or count_documents instead. Please note that $where must be replaced by $expr, $near must be replaced by $geoWithin with $center, and $nearSphere must be replaced by $geoWithin with $centerSphere
  


id,keywords

862,"[{'id': 931, 'name': 'jealousy'}, {'id': 4290, 'name': 'toy'}, {'id': 5202, 'name': 'boy'}, {'id': 6054, 'name': 'friendship'}, {'id': 9713, 'name': 'friends'}, {'id': 9823, 'name': 'rivalry'}, {'id': 165503, 'name': 'boy next door'}, {'id': 170722, 'name': 'new toy'}, {'id': 187065, 'name': 'toy comes to life'}]"

8844,"[{'id': 10090, 'name': 'board game'}, {'id': 10941, 'name': 'disappearance'}, {'id': 15101, 'name': ""based on children's book""}, {'id': 33467, 'name': 'new home'}, {'id': 158086, 'name': 'recluse'}, {'id': 158091, 'name': 'giant insect'}]"

15602,"[{'id': 1495, 'name': 'fishing'}, {'id': 12392, 'name': 'best friend'}, {'id': 179431, 'name': 'duringcreditsstinger'}, {'id': 208510, 'name': 'old men'}]"

31357,"[{'id': 818, 'name': 'based on novel'}, {'id': 10131, 'name': 'interracial relationship'}, {'id': 14768, 'name': 'single mother'}, {'id': 15160, 'name': 'divorce'}, {'id': 33455, 'name': 'chick flick'}]"

11862,"[{'id': 1009, 'name': 'baby'}, {'

21253,"[{'id': 441, 'name': 'assassination'}, {'id': 983, 'name': 'brazilian'}, {'id': 1704, 'name': 'ambassador'}, {'id': 6089, 'name': 'freedom'}, {'id': 8029, 'name': 'drama'}, {'id': 11121, 'name': 'plot'}, {'id': 18263, 'name': 'revolutionary'}]"

6116,"[{'id': 637, 'name': 'pop'}, {'id': 1740, 'name': 'pop culture'}, {'id': 3490, 'name': 'pop star'}]"

9457,"[{'id': 4953, 'name': 'ocean liner'}, {'id': 33696, 'name': 'sea monster'}, {'id': 155508, 'name': 'jewel heist'}, {'id': 196917, 'name': 'armed robbery'}]"

281289,[]

43911,[]

39424,"[{'id': 10183, 'name': 'independent film'}]"

44361,"[{'id': 157499, 'name': 'mother son relationship'}]"

11702,"[{'id': 279, 'name': 'usa'}, {'id': 478, 'name': 'china'}, {'id': 1376, 'name': 'assault rifle'}, {'id': 1589, 'name': 'sniper'}, {'id': 1788, 'name': 'chinatown'}, {'id': 2231, 'name': 'drug dealer'}, {'id': 2708, 'name': 'hitman'}, {'id': 3739, 'name': 'funeral'}, {'id': 8997, 'name': 'conscientious objector'}, {'id': 9748, 'name


26578,"[{'id': 470, 'name': 'spy'}, {'id': 5565, 'name': 'biography'}]"

415072,"[{'id': 178867, 'name': 'lone ranger'}, {'id': 232793, 'name': 'feature version of serial film'}]"

43103,"[{'id': 818, 'name': 'based on novel'}, {'id': 1415, 'name': 'small town'}, {'id': 1936, 'name': 'blackmail'}, {'id': 6093, 'name': 'assault'}, {'id': 11254, 'name': 'loss of virginity'}, {'id': 33720, 'name': 'guilt'}, {'id': 163874, 'name': 'unwed pregnancy'}, {'id': 183126, 'name': 'new job'}, {'id': 188991, 'name': 'drunkenness'}]"

43194,[]

9563,"[{'id': 579, 'name': 'american football'}, {'id': 1482, 'name': 'trainer'}, {'id': 4613, 'name': 'training'}, {'id': 5621, 'name': 'american football coach'}, {'id': 6075, 'name': 'sport'}, {'id': 155802, 'name': 'american football stadium'}]"

1850,"[{'id': 837, 'name': 'show business'}, {'id': 3485, 'name': 'comedian'}, {'id': 5970, 'name': 'wrestling'}]"

926,"[{'id': 2902, 'name': 'space battle'}, {'id': 9831, 'name': 'spaceship'}, {'id': 11931, 'n

6106,"[{'id': 393, 'name': 'civil war'}, {'id': 407, 'name': 'dictator'}, {'id': 736, 'name': 'journalist'}, {'id': 1008, 'name': 'guerrilla'}, {'id': 1014, 'name': 'loss of lover'}, {'id': 2020, 'name': 'revolution'}, {'id': 5299, 'name': 'war correspondent'}, {'id': 5861, 'name': 'civil rights movement '}, {'id': 6760, 'name': 'picture journalist'}, {'id': 7605, 'name': 'el salvador'}, {'id': 7606, 'name': 'dictatorship'}]"

22477,"[{'id': 10183, 'name': 'independent film'}]"

19200,"[{'id': 7002, 'name': 'vigilante'}, {'id': 10183, 'name': 'independent film'}, {'id': 10714, 'name': 'serial killer'}]"

11300,"[{'id': 242, 'name': 'new york'}, {'id': 293, 'name': 'female nudity'}, {'id': 572, 'name': 'sex'}, {'id': 642, 'name': 'robbery'}, {'id': 772, 'name': 'handcuffs'}, {'id': 2483, 'name': 'nudity'}, {'id': 3713, 'name': 'chase'}, {'id': 6149, 'name': 'police'}, {'id': 6259, 'name': 'psychopath'}, {'id': 9935, 'name': 'travel'}, {'id': 10123, 'name': 'dark comedy'}, {'id': 10183, 

...

291189,"[{'id': 15009, 'name': 'criminal'}, {'id': 155808, 'name': 'hometown'}]"

375012,"[{'id': 456, 'name': 'mother'}, {'id': 5600, 'name': 'daughter'}, {'id': 156075, 'name': 'evil'}, {'id': 208289, 'name': '1980s'}, {'id': 232122, 'name': 'tehran'}]"

312849,[]

273912,[]

287719,[]

63004,"[{'id': 2343, 'name': 'magic'}]"

213595,[]

52488,[]

98487,"[{'id': 187056, 'name': 'woman director'}]"

43093,"[{'id': 212, 'name': 'london england'}, {'id': 1299, 'name': 'monster'}, {'id': 1489, 'name': 'river thames'}, {'id': 1618, 'name': 'radiation'}, {'id': 4477, 'name': 'paleontologist'}, {'id': 6978, 'name': 'radium'}, {'id': 8079, 'name': 'cornwall'}, {'id': 10124, 'name': 'laboratory'}, {'id': 11100, 'name': 'giant monster'}, {'id': 12616, 'name': 'dinosaur'}, {'id': 33696, 'name': 'sea monster'}, {'id': 174815, 'name': 'cornwall england'}]"

376311,"[{'id': 1994, 'name': 'wolf'}, {'id': 2035, 'name': 'mythology'}, {'id': 10327, 'name': 'undead'}, {'id': 12564, 'name': 'werewolf'},

399097,"[{'id': 6025, 'name': 'photography'}, {'id': 10683, 'name': 'coming of age'}, {'id': 220448, 'name': 'bipolar disorder'}]"

392554,"[{'id': 187056, 'name': 'woman director'}]"

65442,"[{'id': 12420, 'name': 'unsimulated sex'}]"

198057,"[{'id': 1415, 'name': 'small town'}, {'id': 6018, 'name': 'new hampshire'}, {'id': 169977, 'name': 'small town sheriff'}]"

268956,[]

296472,[]

141267,"[{'id': 4654, 'name': 'undercover agent'}, {'id': 6149, 'name': 'police'}, {'id': 10291, 'name': 'organized crime'}, {'id': 10391, 'name': 'mafia'}, {'id': 14536, 'name': 'crime'}, {'id': 14617, 'name': 'mole'}, {'id': 187056, 'name': 'woman director'}]"

396535,"[{'id': 10349, 'name': 'survival'}, {'id': 10586, 'name': 'korea'}, {'id': 12377, 'name': 'zombie'}, {'id': 13008, 'name': 'train'}, {'id': 158540, 'name': 'south korea'}, {'id': 232649, 'name': 'busan'}]"

138115,[]

138118,[]

136071,[]

133879,"[{'id': 157241, 'name': 'criminal investigation'}, {'id': 187056, 'name': 'woman director


381289,"[{'id': 818, 'name': 'based on novel'}, {'id': 2526, 'name': 'human animal relationship'}, {'id': 5484, 'name': 'reincarnation'}, {'id': 9229, 'name': 'grandparents'}, {'id': 15162, 'name': 'dog'}, {'id': 17994, 'name': 'firecracker'}, {'id': 186846, 'name': 'adaptation'}, {'id': 234523, 'name': 'deflated football'}]"

247446,[]

266558,[]

334890,[]

37376,[]

393521,"[{'id': 1227, 'name': 'cemetery'}, {'id': 3739, 'name': 'funeral'}, {'id': 4523, 'name': 'joint'}, {'id': 8224, 'name': 'cannabis'}, {'id': 10163, 'name': 'cancer'}, {'id': 10226, 'name': 'neighbor'}, {'id': 11612, 'name': 'hospital'}, {'id': 34079, 'name': 'death'}, {'id': 156390, 'name': 'face slap'}, {'id': 159103, 'name': 'mourning'}, {'id': 166124, 'name': 'texting'}, {'id': 225616, 'name': 'smoking a joint'}]"

360814,"[{'id': 5565, 'name': 'biography'}, {'id': 5970, 'name': 'wrestling'}, {'id': 6075, 'name': 'sport'}, {'id': 6683, 'name': 'autobiography'}]"

261439,"[{'id': 497, 'name': 'shakespeare'}, {'

31119,"[{'id': 2766, 'name': 'mutation'}, {'id': 9951, 'name': 'alien'}]"

390293,"[{'id': 10637, 'name': 'food'}, {'id': 40844, 'name': 'sustainable'}, {'id': 208736, 'name': 'bugs'}]"

30633,[]

447091,[]

130300,[]

111042,[]

416951,"[{'id': 5565, 'name': 'biography'}, {'id': 9682, 'name': 'history'}]"

338227,[]

252034,[]

198646,[]

11396,"[{'id': 90, 'name': 'paris'}, {'id': 409, 'name': 'africa'}, {'id': 1454, 'name': 'treasure'}, {'id': 3203, 'name': 'pilot'}, {'id': 190451, 'name': 'dragster'}]"

274991,[]

160124,[]

49579,[]

38332,[]

49574,[]

126555,"[{'id': 187056, 'name': 'woman director'}]"

78595,[]

57204,"[{'id': 1010, 'name': 'bar'}, {'id': 6562, 'name': 'celebrity'}, {'id': 7813, 'name': 'hockey player'}, {'id': 8508, 'name': 'party'}, {'id': 9673, 'name': 'love'}, {'id': 10456, 'name': 'athlete'}, {'id': 10726, 'name': 'gang'}, {'id': 156661, 'name': 'threat'}]"

152989,[]

4644,"[{'id': 10183, 'name': 'independent film'}]"

349177,[]

2132,"[{'id': 2334, 'name

TypeError: documents must be a non-empty list

In [ ]:

# Задание по Pandas
# --------------------------------------------------------------
# Постройте таблицу их тегов и определите top-5 самых популярных

# формируем DataFrame
tags_df = pd.DataFrame(id_tags, columns=['movieid', 'tags'])

# --------------------------------------------------------------
# Ваш код здесь
# сгруппируйте по названию тега с помощью group_by
# для каждого тега вычислите, в каком количестве фильмов он встречается
# оставьте top-5 самых популярных тегов

top_5_tags = tags_df.head(5)

print(top_5_tags)

logger.info("Домашка выполнена!")
# --------------------------------------------------------------